# Is climate an important characteristic of major power outages in the United States?

**Name**: Ripudh Mylapur

**Website Link**: https://ripudhm.github.io/power-outages/

## Code

In [1]:
import pandas as pd
import numpy as np
import os
import folium
import tabulate

import plotly.express as px
pd.options.plotting.backend = 'plotly'

### Cleaning and EDA

In [2]:
import openpyxl
df = pd.read_excel(r"outage.xlsx", index_col = 1, header = 5)
df = df.drop(np.nan)
df = df.drop('variables', axis = 1)

In [3]:
df.shape

(1534, 55)

In [4]:
def join_times(col_date, col_time):
    
    time = df[[col_date, col_time]]
    time = time.assign(date=pd.to_datetime(time[col_date]))
    time['date'] = time['date'].astype(str)
    time = time.assign(datetime=time['date'] + ' ' + time[col_time].astype(str))
    time = time.replace('NaT nan', np.nan)
    time = time.assign(fin=pd.to_datetime(time['datetime']))
    return time['fin']

In [5]:
out_start = join_times('OUTAGE.START.DATE', 'OUTAGE.START.TIME')
rest = join_times('OUTAGE.RESTORATION.DATE', 'OUTAGE.RESTORATION.TIME')
df = df.assign(out_start = out_start)
df = df.assign(rest_start = rest)
df = df.rename(columns = {'out_start': 'OUTAGE.START', 'rest_start': 'OUTAGE.RESTORATION'})
df

YEAR  MONTH    U.S._STATE POSTAL.CODE NERC.REGION  \
OBS                                                           
1.0     2011.0    7.0     Minnesota          MN         MRO   
2.0     2014.0    5.0     Minnesota          MN         MRO   
3.0     2010.0   10.0     Minnesota          MN         MRO   
4.0     2012.0    6.0     Minnesota          MN         MRO   
5.0     2015.0    7.0     Minnesota          MN         MRO   
...        ...    ...           ...         ...         ...   
1530.0  2011.0   12.0  North Dakota          ND         MRO   
1531.0  2006.0    NaN  North Dakota          ND         MRO   
1532.0  2009.0    8.0  South Dakota          SD         RFC   
1533.0  2009.0    8.0  South Dakota          SD         MRO   
1534.0  2000.0    NaN        Alaska          AK        ASCC   

            CLIMATE.REGION ANOMALY.LEVEL CLIMATE.CATEGORY  \
OBS                                                         
1.0     East North Central          -0.3           normal   
2.0     East North Central          -0.1           normal   
3.0     East North Central          -1.5             cold   
4.0     East North Central          -0.1           normal   
5.0     East North Central           1.2             warm   
...                    ...           ...              ...   
1530.0  West North Central          -0.9             cold   
1531.0  West North Central           NaN              NaN   
1532.0  West North Central           0.5             warm   
1533.0  West North Central           0.5             warm   
1534.0                 NaN           NaN              NaN   

          OUTAGE.START.DATE OUTAGE.START.TIME  ... POPDEN_URBAN POPDEN_UC  \
OBS                                            ...                          
1.0     2011-07-01 00:00:00          17:00:00  ...         2279    1700.5   
2.0     2014-05-11 00:00:00          18:38:00  ...         2279    1700.5   
3.0     2010-10-26 00:00:00          20:00:00  ...         2279    1700.5   
4.0     2012-06-19 00:00:00          04:30:00  ...         2279    1700.5   
5.0     2015-07-18 00:00:00          02:00:00  ...         2279    1700.5   
...                     ...               ...  ...          ...       ...   
1530.0  2011-12-06 00:00:00          08:00:00  ...       2192.2    1868.2   
1531.0                  NaN               NaN  ...       2192.2    1868.2   
1532.0  2009-08-29 00:00:00          22:54:00  ...       2038.3    1905.4   
1533.0  2009-08-29 00:00:00          11:00:00  ...       2038.3    1905.4   
1534.0                  NaN               NaN  ...       1802.6      1276   

       POPDEN_RURAL AREAPCT_URBAN AREAPCT_UC   PCT_LAND PCT_WATER_TOT  \
OBS                                                                     
1.0            18.2          2.14        0.6  91.592666      8.407334   
2.0            18.2          2.14        0.6  91.592666      8.407334   
3.0            18.2          2.14        0.6  91.592666      8.407334   
4.0            18.2          2.14        0.6  91.592666      8.407334   
5.0            18.2          2.14        0.6  91.592666      8.407334   
...             ...           ...        ...        ...           ...   
1530.0          3.9          0.27        0.1  97.599649      2.401765   
1531.0          3.9          0.27        0.1  97.599649      2.401765   
1532.0          4.7           0.3       0.15  98.307744      1.692256   
1533.0          4.7           0.3       0.15  98.307744      1.692256   
1534.0          0.4          0.05       0.02  85.761154     14.238846   

        PCT_WATER_INLAND        OUTAGE.START  OUTAGE.RESTORATION  
OBS                                                               
1.0             5.478743 2011-07-01 17:00:00 2011-07-03 20:00:00  
2.0             5.478743 2014-05-11 18:38:00 2014-05-11 18:39:00  
3.0             5.478743 2010-10-26 20:00:00 2010-10-28 22:00:00  
4.0             5.478743 2012-06-19 04:30:00 2012-06-20 23:00:00  
5.0             5.478743 2015-07-18 02:00:

In [6]:
df1 = df[['YEAR', 'MONTH', 'U.S._STATE', 'POSTAL.CODE', 'CLIMATE.REGION','CLIMATE.CATEGORY','PC.REALGSP.STATE',
         'PC.REALGSP.REL', 'POPULATION', 'CUSTOMERS.AFFECTED',  'OUTAGE.START', 'OUTAGE.RESTORATION', 'OUTAGE.DURATION', 'CAUSE.CATEGORY']]
month_count = df1.groupby('MONTH')['YEAR'].count()
fig = month_count.plot()
fig.show()

In [7]:
df1.head()

YEAR  MONTH U.S._STATE POSTAL.CODE      CLIMATE.REGION  \
OBS                                                             
1.0  2011.0    7.0  Minnesota          MN  East North Central   
2.0  2014.0    5.0  Minnesota          MN  East North Central   
3.0  2010.0   10.0  Minnesota          MN  East North Central   
4.0  2012.0    6.0  Minnesota          MN  East North Central   
5.0  2015.0    7.0  Minnesota          MN  East North Central   

    CLIMATE.CATEGORY PC.REALGSP.STATE PC.REALGSP.REL  POPULATION  \
OBS                                                                
1.0           normal            51268       1.077376   5348119.0   
2.0           normal            53499       1.089792   5457125.0   
3.0             cold            50447       1.066826   5310903.0   
4.0           normal            51598       1.071476   5380443.0   
5.0             warm            54431       1.092027   5489594.0   

     CUSTOMERS.AFFECTED        OUTAGE.START  OUTAGE.RESTORATION  \
OBS                                                               
1.0             70000.0 2011-07-01 17:00:00 2011-07-03 20:00:00   
2.0                 NaN 2014-05-11 18:38:00 2014-05-11 18:39:00   
3.0             70000.0 2010-10-26 20:00:00 2010-10-28 22:00:00   
4.0             68200.0 2012-06-19 04:30:00 2012-06-20 23:00:00   
5.0            250000.0 2015-07-18 02:00:00 2015-07-19 07:00:00   

    OUTAGE.DURATION      CAUSE.CATEGORY  
OBS                                      
1.0            3060      severe weather  
2.0               1  intentional attack  
3.0            3000      severe weather  
4.0            2550      severe weather  
5.0            1740      severe weather

In [8]:
state_count = df1.groupby('POSTAL.CODE')['YEAR'].count()
fig = state_count.plot()
m = folium.Map(location=[48, -102], zoom_start=3)
url = (
    "https://raw.githubusercontent.com/python-visualization/folium/main/examples/data"
)
state_geo = f"{url}/us-states.json"

folium.Choropleth(
    geo_data=state_geo,
    name="choropleth",
    data=state_count,
    key_on='feature.id',
    fill_color="YlGn",
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name="Number of Major outages in each state",
).add_to(m)
m._repr_html_()
# f = open("folium_map.html", "w")
# f.write(m._repr_html_())
# f.close()
m

In [9]:
df1.groupby('CLIMATE.CATEGORY')['YEAR'].count()

CLIMATE.CATEGORY
cold      473
normal    744
warm      308
Name: YEAR, dtype: int64

In [10]:
tp = df1.groupby('POPULATION')['YEAR'].count()
fig = px.scatter(tp)
fig.show()

In [11]:
te = df1.groupby('PC.REALGSP.REL')['YEAR'].count()
fig = px.scatter(te)
fig.show()

In [12]:
month_cause = df1.groupby(['MONTH', 'CAUSE.CATEGORY'])['YEAR'].count().reset_index()
month_c = month_cause
fig = month_c.plot(month_c, x = 'MONTH', y = "YEAR", color = 'CAUSE.CATEGORY', title = "Number of major power outages by month and cause")
fig.show()

In [13]:
month = df1.rename(columns = {'YEAR': 'Count'}).groupby(['MONTH'])['Count'].count()
fig = month.plot(title = "Number of major power outages by month", labels = {"variable": "Count of major outages"})
# fig.write_html('month_count.html', include_plotlyjs='cdn')
fig.show()

### Assessment of Missingness

In [14]:
# Pick OUTAGE.DURATION as the column to analyse missingness

In [15]:
missing_percentage = (df1['OUTAGE.DURATION'].isna().sum() / df1.shape[0]) * 100
missing_percentage

3.780964797913951

In [16]:
m1 = df[['OUTAGE.DURATION', 'YEAR', 'MONTH']]
m1_miss = m1[m1['OUTAGE.DURATION'].isna()].groupby('YEAR')['MONTH'].count() /m1[m1['OUTAGE.DURATION'].isna()].groupby('YEAR')['MONTH'].count().sum() 
m1_is = m1[m1['OUTAGE.DURATION'].notna()].groupby('YEAR')['MONTH'].count() / m1[m1['OUTAGE.DURATION'].notna()].groupby('YEAR')['MONTH'].count().sum()
# m1_is_dis = m1_is.groupby('YEAR').count().groupby('YEAR')['MONTH'].count()

to_plot = pd.DataFrame(m1_is)
to_plot['miss'] = m1_miss
to_plot = to_plot.rename(columns={'MONTH': 'not_missing'}).replace(np.nan, 0)
to_plot

not_missing      miss
YEAR                         
2000.0     0.008808  0.122449
2001.0     0.009485  0.020408
2002.0     0.009485  0.040816
2003.0     0.031165  0.000000
2004.0     0.048103  0.000000
2005.0     0.036585  0.020408
2006.0     0.044715  0.000000
2007.0     0.036585  0.040816
2008.0     0.074526  0.020408
2009.0     0.052168  0.020408
2010.0     0.071816  0.000000
2011.0     0.182249  0.000000
2012.0     0.117209  0.020408
2013.0     0.102981  0.020408
2014.0     0.070461  0.163265
2015.0     0.071816  0.265306
2016.0     0.031843  0.244898

In [17]:
fig = to_plot.plot(kind = 'bar')
fig.show()

In [18]:
to_plot['diff'] = abs(to_plot['not_missing'] - to_plot['miss'])
obs_stat = to_plot['diff'].sum() / 2
obs_stat

0.6594767988496212

In [19]:
def perm_test(col_name):
    m1 = df1[['OUTAGE.DURATION', col_name, 'MONTH']]
    m1_miss = m1[m1['OUTAGE.DURATION'].isna()].groupby(col_name)['MONTH'].count() / m1[m1['OUTAGE.DURATION'].isna()].groupby(col_name)['MONTH'].count().sum()
    m1_is = m1[m1['OUTAGE.DURATION'].notna()].groupby(col_name)['MONTH'].count() / m1[m1['OUTAGE.DURATION'].notna()].groupby(col_name)['MONTH'].count().sum()
    # m1_is_dis = m1_is.groupby('YEAR').count().groupby('YEAR')['MONTH'].count()

    to_plot = pd.DataFrame(m1_is)
    to_plot['miss'] = m1_miss
    to_plot = to_plot.rename(columns={'MONTH': 'not_missing'}).replace(np.nan, 0)

    to_plot['diff'] = abs(to_plot['not_missing'] - to_plot['miss'])
    obs_stat = to_plot['diff'].sum() / 2
    obs_stat



    reps = 500
    shuffled = m1.copy()

    tvds = []

    for i in range(reps):
        shuffled['OUTAGE.DURATION'] = np.random.permutation(shuffled['OUTAGE.DURATION'])
        m1_miss = shuffled[shuffled['OUTAGE.DURATION'].isna()].groupby(col_name)['MONTH'].count() / shuffled[shuffled['OUTAGE.DURATION'].isna()].groupby(col_name)['MONTH'].count().sum()
        m1_is = shuffled[shuffled['OUTAGE.DURATION'].notna()].groupby(col_name)['MONTH'].count() / shuffled[shuffled['OUTAGE.DURATION'].notna()].groupby(col_name)['MONTH'].count().sum()
        to_plot = pd.DataFrame(m1_is)
        to_plot['miss'] = m1_miss
        to_plot = to_plot.rename(columns={'MONTH': 'not_missing'}).replace(np.nan, 0)
        to_plot['diff'] = abs(to_plot['not_missing'] - to_plot['miss'])
        tvd_stat = to_plot['diff'].sum() / 2
        tvds.append(tvd_stat)
    tvds = np.array(tvds)
    p_val = (obs_stat >= tvds).mean()
    return p_val, obs_stat

In [20]:
cols = []
p = []
observ = []
for col in df1.columns:
    if col != 'MONTH' and col != 'OUTAGE.DURATION':
        cols.append(col)
        p.append(perm_test(col)[0])
        observ.append((perm_test(col)[1]))

In [28]:
tests = pd.DataFrame(data = {'variable': cols,'p_value': p,'observed_statistic': observ})
tests

variable  p_value  observed_statistic
0                 YEAR    1.000            0.659477
1           U.S._STATE    0.998            0.470204
2          POSTAL.CODE    1.000            0.470204
3       CLIMATE.REGION    1.000            0.317388
4     CLIMATE.CATEGORY    1.000            0.318470
5     PC.REALGSP.STATE    0.992            0.781511
6       PC.REALGSP.REL    0.982            0.781511
7           POPULATION    0.950            0.771984
8   CUSTOMERS.AFFECTED    0.994            0.656115
9         OUTAGE.START    0.176            0.509527
10  OUTAGE.RESTORATION    0.104            0.500000
11      CAUSE.CATEGORY    1.000            0.266799

In [22]:
m2 = df[['OUTAGE.DURATION', 'OUTAGE.RESTORATION', 'MONTH']]
m2

OUTAGE.DURATION  OUTAGE.RESTORATION  MONTH
OBS                                              
1.0               3060 2011-07-03 20:00:00    7.0
2.0                  1 2014-05-11 18:39:00    5.0
3.0               3000 2010-10-28 22:00:00   10.0
4.0               2550 2012-06-20 23:00:00    6.0
5.0               1740 2015-07-19 07:00:00    7.0
...                ...                 ...    ...
1530.0             720 2011-12-06 20:00:00   12.0
1531.0             NaN                 NaT    NaN
1532.0              59 2009-08-29 23:53:00    8.0
1533.0             181 2009-08-29 14:01:00    8.0
1534.0             NaN                 NaT    NaN

[1534 rows x 3 columns]

### Hypothesis Testing

In [23]:
# Test for climate

clim = df.groupby('CLIMATE.CATEGORY')['OUTAGE.DURATION'].agg(['mean', 'count'])
obs = clim['mean'].iloc[-1]
clim

mean  count
CLIMATE.CATEGORY                    
cold              2656.956803    463
normal            2530.980822    730
warm              2817.318021    283

In [24]:
num_reps = 100_000
averages = np.random.choice(df['OUTAGE.DURATION'], size=(num_reps, 283))
averages = np.nanmean(averages, axis=1)
averages

array([2190.260073260073, 2732.934065934066, 1940.078947368421, ...,
       2483.077205882353, 2951.945054945055, 2903.777777777778],
      dtype=object)

In [25]:
(averages <= obs).sum() / num_reps

0.72378

In [26]:
fig = px.histogram(pd.DataFrame(averages), x=0, nbins=50, histnorm='probability', 
                   title='Empirical Distribution of the Average Outage duration in Samples of Size 283')
fig.add_vline(x=df.loc[df['CLIMATE.CATEGORY'] == 'warm', 'OUTAGE.DURATION'].mean(), line_color='red')
fig.show()